In [350]:
import pandas as pd
import seaborn as sns
import numpy as np
from pathlib import Path
from collections import defaultdict
from dateutil import parser
import warnings
warnings.filterwarnings('ignore')


Оставим и сгенерируем признаки, которые мы знаем до следующих игр, т.е если мы будем брать количество пассов на каждую игру для обучения, то при прогнозирование будущей игры мы эти данные не знаем.
Оставим сезоны начиная с 2018, 2023 уходит на валидацию, поэтому при создании признаков не учитываем этот сезон

In [351]:
n = 100 #количество матчей для валидации

pd.set_option('display.max_columns', None)

path_df = '../../../EDA/official/eda_data/games.csv'
path_club = '../../../EDA/official/eda_data/clubs_stat.csv'

df = pd.read_csv(Path(path_df).resolve())
df_club = pd.read_csv(Path(path_club).resolve())

df.head()

match_id  gameweek_id  gameweek_compSeason_label  gameweek_compSeason_id  \
0     93691        12306                       2023                     578   
1     93692        12306                       2023                     578   
2     93693        12306                       2023                     578   
3     93694        12306                       2023                     578   
4     93695        12306                       2023                     578   

   gameweek_gameweek  kickoff_millis               kickoff_label  \
0                 38   1716130800000  Sun 19 May 2024, 16:00 BST   
1                 38   1716130800000  Sun 19 May 2024, 16:00 BST   
2                 38   1716130800000  Sun 19 May 2024, 16:00 BST   
3                 38   1716130800000  Sun 19 May 2024, 16:00 BST   
4                 38   1716130800000  Sun 19 May 2024, 16:00 BST   

   provisionalKickoff_millis    provisionalKickoff_label  \
0              1716130800000  Sun 19 May 2024, 16:00 BST   
1              1716130800000  Sun 19 May 2024, 16:00 BST   
2              1716130800000  Sun 19 May 2024, 16:00 BST   
3              1716130800000  Sun 19 May 2024, 16:00 BST   
4              1716130800000  Sun 19 May 2024, 16:00 BST   

        teams_team_1_name teams_team_1_club_abbr  teams_team_1_club_id  \
0                 Arsenal                    ARS                     1   
1               Brentford                    BRE                   130   
2  Brighton & Hove Albion                    BHA                   131   
3                 Burnley                    BUR                    43   
4                 Chelsea                    CHE                     4   

   teams_score_1  teams_team_2_name teams_team_2_club_abbr  \
0              2            Everton                    EVE   
1              2   Newcastle United                    NEW   
2              0  Manchester United                    MUN   
3              1  Nottingham Forest                    NFO   
4              2        Bournemouth                    BOU   

   teams_team_2_club_id  teams_score_2               ground_name ground_city  \
0                     7              1          Emirates Stadium      London   
1                    23              4   Gtech Community Stadium   Brentford   
2                    12              2  American Express Stadium      Falmer   
3                    15              2                 Turf Moor     Burnley   
4                   127              1           Stamford Bridge      London   

   ground_id outcome  attendance  clock_secs clock_label behindClosedDoors  \
0         52       H     60312.0        5820    90 +7'00             False   
1       4003       A     17124.0        5880    90 +8'00             False   
2       7306       A     31662.0        5760    90 +6'00             False   
3         47       A     21109.0        5640    90 +4'00             False   
4         30       H     39724.0        5880    90 +8'00             False   

      id  team_1_formation_used  team_1_accurate_back_zone_pass  \
0  93691                  433.0                           151.0   
1  93692                  433.0                           214.0   
2  93693                 4231.0                           260.0   
3  93694                  442.0                           159.0   
4  93695                 4231.0                           287.0   

   team_1_total_back_zone_pass  team_1_accurate_pass  team_1_touches  \
0                        157.0                 583.0           831.0   
1                        239.0                 395.0           631.0   
2                        269.0                 495.0           716.0   
3                        168.0                 591.0           809.0   
4                        315.0                 457.0           737.0   

   team_1_total_pass  team_1_backward_pass  team_1_successful_open_play_pass  \
0              653.0                 110.0                             566

In [352]:
home_games = df[['gameweek_compSeason_label', 'teams_team_1_name']].rename(columns={'gameweek_compSeason_label':'Season', 'teams_team_1_name': 'Team'})
away_games = df[['gameweek_compSeason_label', 'teams_team_2_name']].rename(columns={'gameweek_compSeason_label':'Season','teams_team_2_name': 'Team'})

all_games = pd.concat([home_games, away_games])
all_games['Games']=1

result = all_games.groupby(['Season', 'Team']).agg({'Games': 'sum'}).reset_index()
result

Season                     Team  Games
0      2014                  Arsenal     38
1      2014              Aston Villa     38
2      2014                  Burnley     38
3      2014                  Chelsea     38
4      2014           Crystal Palace     38
..      ...                      ...    ...
195    2023        Nottingham Forest     38
196    2023         Sheffield United     38
197    2023        Tottenham Hotspur     38
198    2023          West Ham United     38
199    2023  Wolverhampton Wanderers     38

[200 rows x 3 columns]

team_1_hue - target (Выиграла команда 1 -1, проиграла -0, ничья - 2)

In [353]:
loc_home = [2, 9] + list(range(list(df.columns).index('team_1_formation_used'), list(df.columns).index('team_1_att_cmiss_left')))
loc_away = [2, 13] + list(range(list(df.columns).index('team_2_formation_used'), list(df.columns).index('team_2_att_cmiss_left')))

df_home = df.iloc[:, loc_home]
df_away = df.iloc[:, loc_away]

col_home = [i.replace('team_1_', '') for i in list(df_home.columns)]
col_away = [i.replace('team_2_', '') for i in list(df_away.columns)]

In [354]:
df

match_id  gameweek_id  gameweek_compSeason_label  \
0        93691        12306                       2023   
1        93692        12306                       2023   
2        93693        12306                       2023   
3        93694        12306                       2023   
4        93695        12306                       2023   
...        ...          ...                        ...   
3795      9614          900                       2014   
3796      9615          900                       2014   
3797      9616          900                       2014   
3798      9617          900                       2014   
3799      9613          900                       2014   

      gameweek_compSeason_id  gameweek_gameweek  kickoff_millis  \
0                        578                 38   1716130800000   
1                        578                 38   1716130800000   
2                        578                 38   1716130800000   
3                        578                 38   1716130800000   
4                        578                 38   1716130800000   
...                      ...                ...             ...   
3795                      27                  1   1408197600000   
3796                      27                  1   1408197600000   
3797                      27                  1   1408197600000   
3798                      27                  1   1408197600000   
3799                      27                  1   1408189500000   

                   kickoff_label  provisionalKickoff_millis  \
0     Sun 19 May 2024, 16:00 BST              1716130800000   
1     Sun 19 May 2024, 16:00 BST              1716130800000   
2     Sun 19 May 2024, 16:00 BST              1716130800000   
3     Sun 19 May 2024, 16:00 BST              1716130800000   
4     Sun 19 May 2024, 16:00 BST              1716130800000   
...                          ...                        ...   
3795  Sat 16 Aug 2014, 15:00 BST              1408197600000   
3796  Sat 16 Aug 2014, 15:00 BST              1408197600000   
3797  Sat 16 Aug 2014, 15:00 BST              1408197600000   
3798  Sat 16 Aug 2014, 15:00 BST              1408197600000   
3799  Sat 16 Aug 2014, 12:45 BST              1408189500000   

        provisionalKickoff_label       teams_team_1_name  \
0     Sun 19 May 2024, 16:00 BST                 Arsenal   
1     Sun 19 May 2024, 16:00 BST               Brentford   
2     Sun 19 May 2024, 16:00 BST  Brighton & Hove Albion   
3     Sun 19 May 2024, 16:00 BST                 Burnley   
4     Sun 19 May 2024, 16:00 BST                 Chelsea   
...                          ...                     ...   
3795  Sat 16 Aug 2014, 15:00 BST     Queens Park Rangers   
3796  Sat 16 Aug 2014, 15:00 BST              Stoke City   
3797  Sat 16 Aug 2014, 15:00 BST    West Bromwich Albion   
3798  Sat 16 Aug 2014, 15:00 BST         West Ham United   
3799  Sat 16 Aug 2014, 12:45 BST       Manchester United   

     teams_team_1_club_abbr  teams_team_1_club_id  teams_score_1  \
0                       ARS                     1              2   
1                       BRE                   130              2   
2                       BHA                   131              0   
3                       BUR                    43              1   
4                       CHE                     4              2   
...                     ...                   ...            ...   
3795                    QPR                    17              0   
3796                    STK                    42              0   
3797                    WBA                    36              2   
3798                    WHU                    25              0   
3799                    MUN                    12              1   

      teams_team_2_name teams_team_2_club_abbr  teams_team_2_club_id  \
0               Everton                    EVE                     7   
1      Newcastle United                    NEW                   

In [355]:
df[df['gameweek_compSeason_label'] == 2023]

match_id  gameweek_id  gameweek_compSeason_label  gameweek_compSeason_id  \
0       93691        12306                       2023                     578   
1       93692        12306                       2023                     578   
2       93693        12306                       2023                     578   
3       93694        12306                       2023                     578   
4       93695        12306                       2023                     578   
..        ...          ...                        ...                     ...   
375     93324        12269                       2023                     578   
376     93325        12269                       2023                     578   
377     93327        12269                       2023                     578   
378     93322        12269                       2023                     578   
379     93321        12269                       2023                     578   

     gameweek_gameweek  kickoff_millis               kickoff_label  \
0                   38   1716130800000  Sun 19 May 2024, 16:00 BST   
1                   38   1716130800000  Sun 19 May 2024, 16:00 BST   
2                   38   1716130800000  Sun 19 May 2024, 16:00 BST   
3                   38   1716130800000  Sun 19 May 2024, 16:00 BST   
4                   38   1716130800000  Sun 19 May 2024, 16:00 BST   
..                 ...             ...                         ...   
375                  1   1691848800000  Sat 12 Aug 2023, 15:00 BST   
376                  1   1691848800000  Sat 12 Aug 2023, 15:00 BST   
377                  1   1691848800000  Sat 12 Aug 2023, 15:00 BST   
378                  1   1691841600000  Sat 12 Aug 2023, 13:00 BST   
379                  1   1691780400000  Fri 11 Aug 2023, 20:00 BST   

     provisionalKickoff_millis    provisionalKickoff_label  \
0                1716130800000  Sun 19 May 2024, 16:00 BST   
1                1716130800000  Sun 19 May 2024, 16:00 BST   
2                1716130800000  Sun 19 May 2024, 16:00 BST   
3                1716130800000  Sun 19 May 2024, 16:00 BST   
4                1716130800000  Sun 19 May 2024, 16:00 BST   
..                         ...                         ...   
375              1691848800000  Sat 12 Aug 2023, 15:00 BST   
376              1691848800000  Sat 12 Aug 2023, 15:00 BST   
377              1691848800000  Sat 12 Aug 2023, 15:00 BST   
378              1691841600000  Sat 12 Aug 2023, 13:00 BST   
379              1691780400000  Fri 11 Aug 2023, 20:00 BST   

          teams_team_1_name teams_team_1_club_abbr  teams_team_1_club_id  \
0                   Arsenal                    ARS                     1   
1                 Brentford                    BRE                   130   
2    Brighton & Hove Albion                    BHA                   131   
3                   Burnley                    BUR                    43   
4                   Chelsea                    CHE                     4   
..                      ...                    ...                   ...   
375  Brighton & Hove Albion                    BHA                   131   
376                 Everton                    EVE                     7   
377        Sheffield United                    SHU                    18   
378                 Arsenal                    ARS                     1   
379                 Burnley                    BUR                    43   

     teams_score_1  teams_team_2_name teams_team_2_club_abbr  \
0                2            Everton                    EVE   
1                2   Newcastle United                    NEW   
2                0  Manchester United                    MUN   
3                1  Nottingham Forest                    NFO   
4                2        Bournemouth                    BOU   
..             ...                ...                    ...   
375              4         Luton Town                    LUT   
376              0   

In [356]:
indx_del_home = [i for i, item in enumerate(col_home) if item not in col_away]
indx_del_away = [i for i, item in enumerate(col_away) if item not in col_home]

df_home = df_home.drop(df_home.columns[indx_del_home], axis=1)
df_away = df_away.drop(df_away.columns[indx_del_away], axis=1)

In [357]:
col_home = {i: i.replace('team_1_', '') for i in list(df_home.columns)}
col_away = {i: i.replace('team_2_', '') for i in list(df_away.columns)}

df_home.rename(columns=col_home, inplace=True)
df_away.rename(columns=col_away, inplace=True)

In [358]:
df_home = df_home.groupby(['gameweek_compSeason_label', 'teams_name']).sum().reset_index()
df_away = df_away.groupby(['gameweek_compSeason_label', 'teams_name']).sum().reset_index()

In [359]:
df_games = pd.merge(df_home, df_away, how='left', left_on=['gameweek_compSeason_label', 'teams_name'], right_on=['gameweek_compSeason_label', 'teams_name'])
df_games

gameweek_compSeason_label               teams_name  formation_used_x  \
0                         2014                  Arsenal           72433.0   
1                         2014              Aston Villa           53038.0   
2                         2014                  Burnley           40150.0   
3                         2014                  Chelsea           80389.0   
4                         2014           Crystal Palace           50995.0   
..                         ...                      ...               ...   
195                       2023        Nottingham Forest           49960.0   
196                       2023         Sheffield United           34210.0   
197                       2023        Tottenham Hotspur           72874.0   
198                       2023          West Ham United           76699.0   
199                       2023  Wolverhampton Wanderers           47170.0   

     accurate_back_zone_pass_x  total_back_zone_pass_x  accurate_pass_x  \
0                       3678.0                  3982.0           9401.0   
1                       2871.0                  3246.0           6457.0   
2                       2038.0                  2353.0           4784.0   
3                       3515.0                  3815.0           8677.0   
4                       1917.0                  2225.0           4698.0   
..                         ...                     ...              ...   
195                     2887.0                  3347.0           5635.0   
196                     2337.0                  2755.0           4499.0   
197                     4574.0                  5018.0           9941.0   
198                     3260.0                  3691.0           6096.0   
199                     4299.0                  4803.0           7629.0   

     touches_x  total_pass_x  backward_pass_x  successful_open_play_pass_x  \
0      15146.0       10973.0           1459.0                       9075.0   
1      11751.0        8145.0           1270.0                       6166.0   
2      11003.0        6896.0            916.0                       4525.0   
3      14102.0       10297.0           1637.0                       8375.0   
4      10774.0        6552.0            944.0                       4436.0   
..         ...           ...              ...                          ...   
195    10911.0        7194.0           1103.0                       5340.0   
196     9678.0        6228.0           1009.0                       4219.0   
197    15185.0       11377.0           1822.0                       9476.0   
198    11433.0        7631.0           1281.0                       5809.0   
199    12870.0        9166.0           1505.0                       7313.0   

     open_play_pass_x  possession_percentage_x  leftside_pass_x  \
0             10559.0                   1137.8           2914.0   
1              7697.0                    928.1           1978.0   
2              6469.0                    832.6           1347.0   
3              9870.0                   1077.3           2571.0   
4              6080.0                    852.7           1318.0   
..                ...                      ...              ...   
195            6794.0                    785.5           1718.0   
196            5747.0                    695.3           1257.0   
197           10870.0                   1171.8           2971.0   
198            7224.0                    804.9           1719.0   
199            8741.0                    969.5           2370.0   

     accurate_fwd_zone_pass_x  rightside_pass_x  total_long_balls_x  \
0                      5824.0            2813.0               743.0   
1                      3684.0            1934.0              1331.0   
2                      2843.0            1565.0              1534.0   
3                      5241.0            2508.0              1131.0   
4                      2887.0            1292.0              1331.0   
..         

In [360]:
feature_list_games = ['match_id', 'gameweek_gameweek', 'gameweek_compSeason_label', 'teams_team_1_name', 'teams_team_2_name', 'team_1_hue']

In [361]:
df_simple = df[df['gameweek_compSeason_label']==2023].sort_values(by='match_id')
col_simple = ['match_id', 'gameweek_compSeason_label', 'gameweek_gameweek', 'kickoff_label', 'teams_team_1_name', 'teams_team_2_name', 'ground_name']
df_simple = df_simple[col_simple]
df_simple['kickoff_label']= df_simple['kickoff_label'].apply(lambda x: parser.parse(x))
df_simple.to_csv('data/df_simple.csv', index=False)
df_simple

match_id  gameweek_compSeason_label  gameweek_gameweek  \
379     93321                       2023                  1   
378     93322                       2023                  1   
374     93323                       2023                  1   
375     93324                       2023                  1   
376     93325                       2023                  1   
..        ...                        ...                ...   
5       93696                       2023                 38   
6       93697                       2023                 38   
7       93698                       2023                 38   
8       93699                       2023                 38   
9       93700                       2023                 38   

           kickoff_label       teams_team_1_name        teams_team_2_name  \
379  2023-08-11 20:00:00                 Burnley          Manchester City   
378  2023-08-12 13:00:00                 Arsenal        Nottingham Forest   
374  2023-08-12 15:00:00             Bournemouth          West Ham United   
375  2023-08-12 15:00:00  Brighton & Hove Albion               Luton Town   
376  2023-08-12 15:00:00                 Everton                   Fulham   
..                   ...                     ...                      ...   
5    2024-05-19 16:00:00          Crystal Palace              Aston Villa   
6    2024-05-19 16:00:00               Liverpool  Wolverhampton Wanderers   
7    2024-05-19 16:00:00              Luton Town                   Fulham   
8    2024-05-19 16:00:00         Manchester City          West Ham United   
9    2024-05-19 16:00:00        Sheffield United        Tottenham Hotspur   

                  ground_name  
379                 Turf Moor  
378          Emirates Stadium  
374          Vitality Stadium  
375  American Express Stadium  
376             Goodison Park  
..                        ...  
5               Selhurst Park  
6                     Anfield  
7             Kenilworth Road  
8              Etihad Stadium  
9                Bramall Lane  

[380 rows x 7 columns]

In [362]:
#Датасет для бейзлайна
df[feature_list_games].to_csv(Path('data/base_line.csv').resolve(), index=False)
df.drop('ground_name', axis=1, inplace=True)

In [363]:
df['month'] = df['provisionalKickoff_label'].apply(lambda x: x.split()[2])
df['day_week'] = df['provisionalKickoff_label'].apply(lambda x: x.split()[0])
df['hour'] = df['provisionalKickoff_label'].apply(lambda x: x.split()[4].split(':')[0])

feature_list_games.extend(['kickoff_label', 'month', 'day_week', 'hour', 'ground_id'])

In [364]:
df_club.head()

season_id club_name club_abbr  club_id  _accurate_back_zone_pass  \
0        578   Arsenal       ARS      1.0                    7989.0   
1        489   Arsenal       ARS      1.0                    7609.0   
2        418   Arsenal       ARS      1.0                    7337.0   
3        363   Arsenal       ARS      1.0                    8985.0   
4        274   Arsenal       ARS      1.0                    8703.0   

   _accurate_chipped_pass  _accurate_corners_intobox  _accurate_cross  \
0                   601.0                       64.0            174.0   
1                   651.0                       38.0            138.0   
2                   583.0                       49.0            149.0   
3                   645.0                       38.0            161.0   
4                   628.0                       56.0            141.0   

   _accurate_cross_nocorner  _accurate_flick_on  _accurate_freekick_cross  \
0                     112.0                25.0                      12.0   
1                     103.0                20.0                      17.0   
2                     103.0                24.0                       6.0   
3                     123.0                38.0                      15.0   
4                      90.0                30.0                       5.0   

   _accurate_fwd_zone_pass  _accurate_goal_kicks  _accurate_keeper_sweeper  \
0                  10463.0                 152.0                      21.0   
1                   9987.0                 113.0                      15.0   
2                   8066.0                 132.0                      21.0   
3                   8294.0                 142.0                      12.0   
4                   7020.0                 221.0                      17.0   

   _accurate_keeper_throws  _accurate_launches  _accurate_layoffs  \
0                    187.0               150.0              198.0   
1                    168.0                66.0              158.0   
2                    174.0                90.0              190.0   
3                    205.0                79.0              200.0   
4                    231.0                96.0              179.0   

   _accurate_long_balls  _accurate_pass  _accurate_pull_back  \
0                 726.0         18278.0                 21.0   
1                 845.0         17458.0                 13.0   
2                 790.0         15254.0                 20.0   
3                 855.0         17118.0                 14.0   
4                 960.0         15582.0                 12.0   

   _accurate_through_ball  _accurate_throws  _aerial_lost  _aerial_won  \
0                    51.0             455.0         509.0        515.0   
1                    38.0             517.0         564.0        490.0   
2                    26.0             598.0         577.0        470.0   
3                    20.0             557.0         604.0        515.0   
4                    16.0             680.0         599.0        513.0   

   _attempted_tackle_foul  _attempts_conceded_ibox  _attempts_conceded_obox  \
0                   267.0                    196.0                    128.0   
1                   195.0                    244.0                     99.0   
2                   194.0                    264.0                    162.0   
3                   184.0                    263.0                    156.0   
4                   251.0                    344.0                    209.0   

   _attempts_ibox  _attempts_obox  _att_assist_openplay  _att_assist_setplay  \
0           468.0           189.0                 405.0                 46.0   
1           414.0           179.0                 337.0                 42.0   
2           372.0           217.0                 362.0                 34.0   
3           293.0           166.0                 266.0                 28.0   
4           281.0           125.0                 218.0                 46.0   

   _

In [365]:
df_club.drop(labels=['_attendance_count', '_attendance_total', '_attendance_average',	'_attendance_highest', '_attendance_lowest'], axis=1, inplace=True)

In [366]:
list_na = list(df_club.isna().sum()[df_club.isna().sum() > 0].index)

In [367]:
df_club[list_na] = df_club[list_na].fillna(df_club[df_club['season']!=2023][list_na].mean())

In [368]:
cols_mean = list(df_club.columns)[4:-1]
cols_mean = ['club_name'] + cols_mean

In [369]:
df_club_lag = df_club.drop(labels=['season_id', 'club_abbr', 'club_id'], axis=1)
df_club_lag['season'] = df_club_lag['season'] + 1
df_club_lag

club_name  _accurate_back_zone_pass  \
0                    Arsenal                    7989.0   
1                    Arsenal                    7609.0   
2                    Arsenal                    7337.0   
3                    Arsenal                    8985.0   
4                    Arsenal                    8703.0   
..                       ...                       ...   
195  Wolverhampton Wanderers                    7832.0   
196  Wolverhampton Wanderers                    7960.0   
197  Wolverhampton Wanderers                    7596.0   
198  Wolverhampton Wanderers                    6941.0   
199  Wolverhampton Wanderers                    6535.0   

     _accurate_chipped_pass  _accurate_corners_intobox  _accurate_cross  \
0                     601.0                       64.0            174.0   
1                     651.0                       38.0            138.0   
2                     583.0                       49.0            149.0   
3                     645.0                       38.0            161.0   
4                     628.0                       56.0            141.0   
..                      ...                        ...              ...   
195                   730.0                       52.0            156.0   
196                   737.0                       38.0            137.0   
197                   843.0                       44.0            171.0   
198                  1021.0                       41.0            177.0   
199                   862.0                       41.0            157.0   

     _accurate_cross_nocorner  _accurate_flick_on  _accurate_freekick_cross  \
0                       112.0                25.0                      12.0   
1                       103.0                20.0                      17.0   
2                       103.0                24.0                       6.0   
3                       123.0                38.0                      15.0   
4                        90.0                30.0                       5.0   
..                        ...                 ...                       ...   
195                     108.0                47.0                      11.0   
196                      99.0                45.0                      14.0   
197                     128.0                45.0                      20.0   
198                     138.0                74.0                      21.0   
199                     118.0                53.0                      18.0   

     _accurate_fwd_zone_pass  _accurate_goal_kicks  _accurate_keeper_sweeper  \
0                    10463.0                 152.0                      21.0   
1                     9987.0                 113.0                      15.0   
2                     8066.0                 132.0                      21.0   
3                     8294.0                 142.0                      12.0   
4                     7020.0                 221.0                      17.0   
..                       ...                   ...                       ...   
195                   5914.0                 161.0                      13.0   
196                   6413.0                 200.0                      32.0   
197                   7145.0                 196.0                       4.0   
198                   6522.0                 171.0                       3.0   
199                   6612.0                 167.0                       2.0   

     _accurate_keeper_throws  _accurate_launches  _accurate_layoffs  \
0                      187.0               150.0              198.0   
1                      168.0                66.0              158.0   
2                      174.0                90.0              190.0   
3                      205.0                79.0              200.0   
4                      231.0                96.0              179.0   
..                       ...                 ...                ...   
195           

In [370]:
df_num_mean = df_club[df_club['season']!=2023][cols_mean].groupby('club_name', as_index=False).mean()

In [371]:
df_num_mean.head()

club_name  _accurate_back_zone_pass  _accurate_chipped_pass  \
0                   Arsenal               7925.444444              693.777778   
1               Aston Villa               5937.666667              652.000000   
2               Bournemouth               6257.000000              557.333333   
3                 Brentford               5790.000000              742.000000   
4  Brighton and Hove Albion               7448.333333              669.166667   

   _accurate_corners_intobox  _accurate_cross  _accurate_cross_nocorner  \
0                  51.222222       150.333333                101.111111   
1                  49.333333       162.500000                115.000000   
2                  41.333333       145.333333                105.833333   
3                  49.500000       163.000000                115.000000   
4                  58.500000       166.166667                109.166667   

   _accurate_flick_on  _accurate_freekick_cross  _accurate_fwd_zone_pass  \
0           63.444444                 10.666667              9513.000000   
1           76.500000                 17.500000              6279.333333   
2           66.833333                 14.166667              6302.333333   
3           79.000000                 15.000000              4957.000000   
4           75.833333                 13.666667              6839.833333   

   _accurate_goal_kicks  _accurate_keeper_sweeper  _accurate_keeper_throws  \
0            154.333333                 21.777778               196.444444   
1            178.666667                 19.000000               159.666667   
2            175.166667                 13.500000               194.166667   
3            179.000000                 22.000000               170.500000   
4            178.000000                  7.333333               164.500000   

   _accurate_launches  _accurate_layoffs  _accurate_long_balls  \
0          116.444444         396.777778            926.333333   
1          193.666667         251.000000           1046.166667   
2          185.500000         262.500000            973.666667   
3          148.000000         120.500000            971.000000   
4          153.000000         201.666667           1077.500000   

   _accurate_pass  _accurate_pull_back  _accurate_through_ball  \
0    17288.111111            18.444444               34.000000   
1    12054.500000             9.000000               15.666667   
2    12414.000000            10.166667               18.166667   
3    10584.000000             5.500000               24.500000   
4    14122.000000            10.000000               16.833333   

   _accurate_throws  _aerial_lost  _aerial_won  _attempted_tackle_foul  \
0        646.333333    599.555556   574.333333              209.888889   
1        644.166667    631.000000   646.833333              229.000000   
2        694.166667    684.500000   648.500000              174.500000   
3        579.000000    677.500000   694.500000              194.000000   
4        647.833333    610.500000   652.666667              231.166667   

   _attempts_conceded_ibox  _attempts_conceded_obox  _attempts_ibox  \
0               271.000000               168.777778      327.788959   
1               326.666667               180.833333      245.508386   
2               332.500000               210.333333      264.675052   
3               317.000000               216.500000      308.000000   
4               302.833333               176.000000      296.166667   

   _attempts_obox  _att_assist_openplay  _att_assist_setplay  _att_bx_centre  \
0      173.937107            321.777778            38.222222      195.333333   
1      139.286164            261.000000            46.333333      156.833333   
2      156.952830            248.500000            38.333333      156.833333   
3      117.000000            212.000000            51.500000      168.000000   
4      171.500000            271.666667            50.166667      177.166667   

   _att

In [372]:
df_num_mean.to_csv(Path('data/club_mean.csv').resolve(), index=False)


In [373]:
# how left
df_1 = df[feature_list_games].merge(df_num_mean,
                                    left_on='teams_team_1_name',
                                    right_on='club_name',
                                    how='left')
df_1 = df_1.merge(df_num_mean,
                  left_on='teams_team_2_name',
                  right_on='club_name',
                  suffixes=('_team_1', '_team_2'),
                  how='left')
df_1.drop(['club_name_team_1',
           'club_name_team_2'], axis=1, inplace=True)
df_1

match_id  gameweek_gameweek  gameweek_compSeason_label  \
0        93691                 38                       2023   
1        93692                 38                       2023   
2        93693                 38                       2023   
3        93694                 38                       2023   
4        93695                 38                       2023   
...        ...                ...                        ...   
3795      9614                  1                       2014   
3796      9615                  1                       2014   
3797      9616                  1                       2014   
3798      9617                  1                       2014   
3799      9613                  1                       2014   

           teams_team_1_name  teams_team_2_name  team_1_hue  \
0                    Arsenal            Everton           1   
1                  Brentford   Newcastle United           0   
2     Brighton & Hove Albion  Manchester United           0   
3                    Burnley  Nottingham Forest           0   
4                    Chelsea        Bournemouth           1   
...                      ...                ...         ...   
3795     Queens Park Rangers          Hull City           0   
3796              Stoke City        Aston Villa           0   
3797    West Bromwich Albion         Sunderland           2   
3798         West Ham United  Tottenham Hotspur           0   
3799       Manchester United       Swansea City           0   

                   kickoff_label month day_week hour  ground_id  \
0     Sun 19 May 2024, 16:00 BST   May      Sun   16         52   
1     Sun 19 May 2024, 16:00 BST   May      Sun   16       4003   
2     Sun 19 May 2024, 16:00 BST   May      Sun   16       7306   
3     Sun 19 May 2024, 16:00 BST   May      Sun   16         47   
4     Sun 19 May 2024, 16:00 BST   May      Sun   16         30   
...                          ...   ...      ...  ...        ...   
3795  Sat 16 Aug 2014, 15:00 BST   Aug      Sat   15         46   
3796  Sat 16 Aug 2014, 15:00 BST   Aug      Sat   15        435   
3797  Sat 16 Aug 2014, 15:00 BST   Aug      Sat   15         33   
3798  Sat 16 Aug 2014, 15:00 BST   Aug      Sat   15         44   
3799  Sat 16 Aug 2014, 12:45 BST   Aug      Sat   12         42   

      _accurate_back_zone_pass_team_1  _accurate_chipped_pass_team_1  \
0                         7925.444444                     693.777778   
1                         5790.000000                     742.000000   
2                                 NaN                            NaN   
3                         4202.000000                     598.428571   
4                         8834.444444                     771.666667   
...                               ...                            ...   
3795                      4135.000000                     574.000000   
3796                      5308.250000                     590.500000   
3797                      4240.400000                     498.000000   
3798                      5533.444444                     625.555556   
3799                      7671.666667                     724.222222   

      _accurate_corners_intobox_team_1  _accurate_cross_team_1  \
0                            51.222222              150.333333   
1                            49.500000              163.000000   
2                                  NaN                     NaN   
3                            52.285714              171.428571   
4                            57.777778              158.888889   
...                                ...                     ...   
3795                         67.000000              182.000000   
3796                         53.000000              157.750000   
3797                         47.000000              172.200000   
3798                         57.444444              176.333333   
3799                         49.000000              153.444444   

      _accurate_c

In [374]:
df_1[df_1['gameweek_compSeason_label']==2023].shape

(380, 431)

In [375]:
df_general = pd.merge(df_1, df_club_lag, left_on=['teams_team_1_name', 'gameweek_compSeason_label'], right_on=['club_name', 'season'], how='left')
df_general = pd.merge(df_general, df_club_lag, left_on=['teams_team_2_name', 'gameweek_compSeason_label'], right_on=['club_name', 'season'], how='left', suffixes=('_lag_team1', '_lag_team2'))

In [376]:
df_general.sort_values(by=['match_id'], ascending=False , inplace=True)
df_general

match_id  gameweek_gameweek  gameweek_compSeason_label  \
9        93700                 38                       2023   
8        93699                 38                       2023   
7        93698                 38                       2023   
6        93697                 38                       2023   
5        93696                 38                       2023   
...        ...                ...                        ...   
3796      9615                  1                       2014   
3795      9614                  1                       2014   
3799      9613                  1                       2014   
3794      9612                  1                       2014   
3793      9611                  1                       2014   

        teams_team_1_name        teams_team_2_name  team_1_hue  \
9        Sheffield United        Tottenham Hotspur           0   
8         Manchester City          West Ham United           1   
7              Luton Town                   Fulham           0   
6               Liverpool  Wolverhampton Wanderers           1   
5          Crystal Palace              Aston Villa           1   
...                   ...                      ...         ...   
3796           Stoke City              Aston Villa           0   
3795  Queens Park Rangers                Hull City           0   
3799    Manchester United             Swansea City           0   
3794       Leicester City                  Everton           2   
3793              Arsenal           Crystal Palace           1   

                   kickoff_label month day_week hour  ground_id  \
9     Sun 19 May 2024, 16:00 BST   May      Sun   16       2003   
8     Sun 19 May 2024, 16:00 BST   May      Sun   16        457   
7     Sun 19 May 2024, 16:00 BST   May      Sun   16       2025   
6     Sun 19 May 2024, 16:00 BST   May      Sun   16       7305   
5     Sun 19 May 2024, 16:00 BST   May      Sun   16         45   
...                          ...   ...      ...  ...        ...   
3796  Sat 16 Aug 2014, 15:00 BST   Aug      Sat   15        435   
3795  Sat 16 Aug 2014, 15:00 BST   Aug      Sat   15         46   
3799  Sat 16 Aug 2014, 12:45 BST   Aug      Sat   12         42   
3794  Sat 16 Aug 2014, 15:00 BST   Aug      Sat   15         49   
3793  Sat 16 Aug 2014, 17:30 BST   Aug      Sat   17         52   

      _accurate_back_zone_pass_team_1  _accurate_chipped_pass_team_1  \
9                         4923.500000                     555.500000   
8                         9053.555556                     732.666667   
7                                 NaN                            NaN   
6                         8856.333333                     844.333333   
5                         5503.111111                     538.000000   
...                               ...                            ...   
3796                      5308.250000                     590.500000   
3795                      4135.000000                     574.000000   
3799                      7671.666667                     724.222222   
3794                      6395.666667                     663.222222   
3793                      7925.444444                     693.777778   

      _accurate_corners_intobox_team_1  _accurate_cross_team_1  \
9                            48.500000              161.500000   
8                            72.555556              173.000000   
7                                  NaN                     NaN   
6                            62.111111              180.222222   
5                            55.666667              165.888889   
...                                ...                     ...   
3796                         53.000000              157.750000   
3795                         67.000000              182.000000   
3799                         49.000000              153.444444   
3794                         46.666667              146.777778   
3793                         51.222222          

In [377]:
df_general.drop(['season_lag_team2', 'season_lag_team1', 'club_name_lag_team1', 'club_name_lag_team2'], axis=1, inplace=True)

In [378]:
df_general.shape

(3800, 851)

In [379]:
df_general.to_csv('data/df_res.csv', index=False)

In [380]:
df_1.to_csv('data/df_1.csv', index=False)

In [381]:
df_1

match_id  gameweek_gameweek  gameweek_compSeason_label  \
0        93691                 38                       2023   
1        93692                 38                       2023   
2        93693                 38                       2023   
3        93694                 38                       2023   
4        93695                 38                       2023   
...        ...                ...                        ...   
3795      9614                  1                       2014   
3796      9615                  1                       2014   
3797      9616                  1                       2014   
3798      9617                  1                       2014   
3799      9613                  1                       2014   

           teams_team_1_name  teams_team_2_name  team_1_hue  \
0                    Arsenal            Everton           1   
1                  Brentford   Newcastle United           0   
2     Brighton & Hove Albion  Manchester United           0   
3                    Burnley  Nottingham Forest           0   
4                    Chelsea        Bournemouth           1   
...                      ...                ...         ...   
3795     Queens Park Rangers          Hull City           0   
3796              Stoke City        Aston Villa           0   
3797    West Bromwich Albion         Sunderland           2   
3798         West Ham United  Tottenham Hotspur           0   
3799       Manchester United       Swansea City           0   

                   kickoff_label month day_week hour  ground_id  \
0     Sun 19 May 2024, 16:00 BST   May      Sun   16         52   
1     Sun 19 May 2024, 16:00 BST   May      Sun   16       4003   
2     Sun 19 May 2024, 16:00 BST   May      Sun   16       7306   
3     Sun 19 May 2024, 16:00 BST   May      Sun   16         47   
4     Sun 19 May 2024, 16:00 BST   May      Sun   16         30   
...                          ...   ...      ...  ...        ...   
3795  Sat 16 Aug 2014, 15:00 BST   Aug      Sat   15         46   
3796  Sat 16 Aug 2014, 15:00 BST   Aug      Sat   15        435   
3797  Sat 16 Aug 2014, 15:00 BST   Aug      Sat   15         33   
3798  Sat 16 Aug 2014, 15:00 BST   Aug      Sat   15         44   
3799  Sat 16 Aug 2014, 12:45 BST   Aug      Sat   12         42   

      _accurate_back_zone_pass_team_1  _accurate_chipped_pass_team_1  \
0                         7925.444444                     693.777778   
1                         5790.000000                     742.000000   
2                                 NaN                            NaN   
3                         4202.000000                     598.428571   
4                         8834.444444                     771.666667   
...                               ...                            ...   
3795                      4135.000000                     574.000000   
3796                      5308.250000                     590.500000   
3797                      4240.400000                     498.000000   
3798                      5533.444444                     625.555556   
3799                      7671.666667                     724.222222   

      _accurate_corners_intobox_team_1  _accurate_cross_team_1  \
0                            51.222222              150.333333   
1                            49.500000              163.000000   
2                                  NaN                     NaN   
3                            52.285714              171.428571   
4                            57.777778              158.888889   
...                                ...                     ...   
3795                         67.000000              182.000000   
3796                         53.000000              157.750000   
3797                         47.000000              172.200000   
3798                         57.444444              176.333333   
3799                         49.000000              153.444444   

      _accurate_c

## Prepare players

In [382]:
player_team = '../../../parsers/official/data/player_team.csv'
df_player = '../../../EDA/official/eda_data/players_stat.csv'
df_goal = '../../../parsers/official/data/goalkippers.csv'


player_team = pd.read_csv(Path(player_team).resolve())
df_player = pd.read_csv(Path(df_player).resolve())
df_goal = pd.read_csv(Path(df_goal).resolve())

In [383]:
player_team['team'].unique()

array(['Arsenal', 'Aston Villa', 'Bournemouth', 'Brentford',
       'Brighton and Hove Albion', 'Burnley', 'Chelsea', 'Crystal Palace',
       'Everton', 'Fulham', 'Liverpool', 'Luton Town', 'Manchester City',
       'Manchester United', 'Newcastle United', 'Nottingham Forest',
       'Sheffield United', 'Tottenham Hotspur', 'West Ham United',
       'Wolverhampton Wanderers', 'Leeds United', 'Leicester City',
       'Southampton', 'Norwich City', 'Watford', 'West Bromwich Albion',
       'Cardiff City', 'Huddersfield Town', 'Stoke City', 'Swansea City',
       'Hull City', 'Middlesbrough', 'Sunderland', 'Queens Park Rangers'],
      dtype=object)

In [384]:
player_team.groupby(['team', 'season']).count()['player_id'].min()

20

In [385]:
player_team.groupby(['team', 'season']).count()['player_id'].max()

61

In [386]:
player_team

season             team  player_id position               name  \
0       2023          Arsenal     284417        D          Ben White   
1       2023          Arsenal     202648        D  Gabriel Magalhães   
2       2023          Arsenal     313972        D     William Saliba   
3       2023          Arsenal     337014        D       Jakub Kiwior   
4       2023          Arsenal     288984        D  Takehiro Tomiyasu   
...      ...              ...        ...      ...                ...   
5346    2014  West Ham United      14145        F     Enner Valencia   
5347    2014  West Ham United       6548        F         Elliot Lee   
5348    2014  West Ham United       6535        M     Ravel Morrison   
5349    2014  West Ham United       6545        F     Ricardo Vaz Tê   
5350    2014  West Ham United       6537        M      Mohamed Diamé   

      appearances  height  weight  goals  assists  tackles  shots  keyPasses  \
0              37   186.0    76.0      4        4       48     13         39   
1              36   190.0    78.0      4        0       48     31          3   
2              38   192.0    92.0      2        1       41     10          6   
3              20   189.0    75.0      1        3       20      6          6   
4              22   187.0    70.0      2        1       20     17          6   
...           ...     ...     ...    ...      ...      ...    ...        ...   
5346           32   177.0    74.0      4        3       30     72         18   
5347            1   180.0    72.0      0        0        1      0          0   
5348            1   175.0    71.0      0        0        0      0          0   
5349            4   188.0    80.0      0        0        4      7          3   
5350            3   184.0    86.0      0        0        5      1          0   

      cleanSheets  
0              13  
1              15  
2              18  
3               5  
4               3  
...           ...  
5346            2  
5347            0  
5348            0  
5349            0  
5350            0  

[5351 rows x 14 columns]

In [387]:
#min amount defenders
player_team[player_team['position']=='D'].groupby(['team', 'season']).count()['player_id'].min()

7

In [388]:
#Min amount forwards
player_team[player_team['position']=='F'].groupby(['team', 'season']).count()['player_id'].min()

3

In [389]:
#Min amount midlefielders
player_team[player_team['position']=='M'].groupby(['team', 'season']).count()['player_id'].min()

6

Формируем датасет, где объект - команда за какой то сезон, в котором информация о игроках и их статистика. Игроков мы будем ранжировать, что бы было все одинаково, отбирать мы будем по количеству игр за сезон. Сначала будут идту 3 форварда, потом 6 мидлов и 7 защитников, потом вратарь и в конце менеджер.
Что бы не было утечки сдвигаем статистику на год назад

In [390]:
player_team['season'].max()

2023

In [391]:
player_team_t = player_team.copy()

In [392]:
player_team_t[player_team_t['name']=='Ben White']

season                      team  player_id position       name  \
0       2023                   Arsenal     284417        D  Ben White   
525     2022                   Arsenal     284417        D  Ben White   
1105    2021                   Arsenal     284417        D  Ben White   
1883    2020  Brighton and Hove Albion     186780        D  Ben White   

      appearances  height  weight  goals  assists  tackles  shots  keyPasses  \
0              37   186.0    76.0      4        4       48     13         39   
525            38   186.0    76.0      2        5       60     10         26   
1105           32   186.0    76.0      0        0       44     12         13   
1883           36   186.0    76.0      0        0       49     10          8   

      cleanSheets  
0              13  
525             9  
1105           13  
1883           11

In [393]:
player_team_t['season'] = player_team_t['season']+1
player_team_t[player_team_t['name']=='Ben White']

season                      team  player_id position       name  \
0       2024                   Arsenal     284417        D  Ben White   
525     2023                   Arsenal     284417        D  Ben White   
1105    2022                   Arsenal     284417        D  Ben White   
1883    2021  Brighton and Hove Albion     186780        D  Ben White   

      appearances  height  weight  goals  assists  tackles  shots  keyPasses  \
0              37   186.0    76.0      4        4       48     13         39   
525            38   186.0    76.0      2        5       60     10         26   
1105           32   186.0    76.0      0        0       44     12         13   
1883           36   186.0    76.0      0        0       49     10          8   

      cleanSheets  
0              13  
525             9  
1105           13  
1883           11

In [394]:
player_team[player_team['name']=='Ben White']

season                      team  player_id position       name  \
0       2023                   Arsenal     284417        D  Ben White   
525     2022                   Arsenal     284417        D  Ben White   
1105    2021                   Arsenal     284417        D  Ben White   
1883    2020  Brighton and Hove Albion     186780        D  Ben White   

      appearances  height  weight  goals  assists  tackles  shots  keyPasses  \
0              37   186.0    76.0      4        4       48     13         39   
525            38   186.0    76.0      2        5       60     10         26   
1105           32   186.0    76.0      0        0       44     12         13   
1883           36   186.0    76.0      0        0       49     10          8   

      cleanSheets  
0              13  
525             9  
1105           13  
1883           11

In [395]:
#Cдвигаем статистику на год
df_player_lag = pd.merge(player_team[['season', 'team', 'player_id', 'position', 'name']], player_team_t.drop(['player_id', 'position', 'team'], axis=1), on=['season', 'name'], how='left')
df_player_lag = df_player_lag[df_player_lag['season'] != df_player_lag['season'].min()]
df_player_lag

season             team  player_id position               name  \
0       2023          Arsenal     284417        D          Ben White   
1       2023          Arsenal     202648        D  Gabriel Magalhães   
2       2023          Arsenal     313972        D     William Saliba   
3       2023          Arsenal     337014        D       Jakub Kiwior   
4       2023          Arsenal     288984        D  Takehiro Tomiyasu   
...      ...              ...        ...      ...                ...   
5087    2015  West Ham United      14143        F       Mauro Zárate   
5088    2015  West Ham United      14143        F       Mauro Zárate   
5089    2015  West Ham United       6544        F       Modibo Maiga   
5090    2015  West Ham United       6532        M        Kevin Nolan   
5091    2015  West Ham United       6533        M     Matthew Jarvis   

      appearances  height  weight  goals  assists  tackles  shots  keyPasses  \
0            38.0   186.0    76.0    2.0      5.0     60.0   10.0       26.0   
1            38.0   190.0    78.0    3.0      0.0     48.0   32.0        5.0   
2            27.0   192.0    92.0    2.0      1.0     34.0    6.0        6.0   
3             7.0   189.0    75.0    1.0      0.0      7.0    1.0        1.0   
4            21.0   187.0    70.0    0.0      1.0     27.0    3.0        4.0   
...           ...     ...     ...    ...      ...      ...    ...        ...   
5087          4.0   176.0    76.0    0.0      0.0      1.0    4.0        0.0   
5088          7.0   176.0    76.0    2.0      1.0      9.0   13.0        7.0   
5089          NaN     NaN     NaN    NaN      NaN      NaN    NaN        NaN   
5090         29.0   183.0    85.0    1.0      1.0     38.0   31.0       12.0   
5091         11.0   173.0    70.0    0.0      0.0      7.0    5.0       10.0   

      cleanSheets  
0             9.0  
1            14.0  
2            11.0  
3             1.0  
4             1.0  
...           ...  
5087          0.0  
5088          0.0  
5089          NaN  
5090          2.0  
5091          0.0  

[5092 rows x 14 columns]

In [396]:
df_goal_t = df_goal.copy()
df_goal_t['season'] = df_goal_t['season'] + 1
df_goal_lag = pd.merge(df_goal[['season', 'team', 'player_id', 'position', 'name']],
                       df_goal_t.drop(['player_id', 'position', 'team'], axis=1),
                       on=['season', 'name'], how='left')
df_goal_lag = df_goal_lag[df_goal_lag['season'] != df_goal_lag['season'].min()]
df_goal_lag

season                  team  player_id position                name  \
0      2023               Arsenal     288169        G      Aaron Ramsdale   
1      2023               Arsenal     345065        G          David Raya   
2      2023           Aston Villa     252275        G   Emiliano Martínez   
3      2023           Aston Villa     312582        G         Robin Olsen   
4      2023           Aston Villa     312582        G         Robin Olsen   
..      ...                   ...        ...      ...                 ...   
400    2015               Watford      20250        G  Giedrius Arlauskis   
401    2015  West Bromwich Albion       6513        G          Ben Foster   
402    2015  West Bromwich Albion       5819        G         Boaz Myhill   
403    2015       West Ham United       6787        G              Adrián   
404    2015       West Ham United     132466        G     Darren Randolph   

     appearances  height  weight  cleanSheets  saves  goalsConceded  
0           38.0   188.0    88.0         14.0   95.0           43.0  
1           38.0   183.0    80.0         12.0  154.0           46.0  
2           36.0   195.0    88.0         11.0   98.0           38.0  
3            4.0   198.0    89.0          1.0   11.0            8.0  
4            4.0   198.0    89.0          1.0   11.0            8.0  
..           ...     ...     ...          ...    ...            ...  
400          NaN     NaN     NaN          NaN    NaN            NaN  
401         28.0   193.0    79.0         11.0   75.0           34.0  
402         11.0   191.0    91.0          4.0   56.0           17.0  
403         38.0   190.0    80.0          8.0  129.0           47.0  
404          NaN     NaN     NaN          NaN    NaN            NaN  

[405 rows x 11 columns]

In [397]:
def flatten_team(df, team_dict, col, type):
    
    df = df[col]
    for i in range(len(df)):

        for j in range(len(col)):
            team_dict[type + '_' + str(i) + '_' + col[j]].append(df.iloc[i, j])

    return team_dict
        

In [398]:
team_dict = defaultdict(list)
col_players = ['name', 'appearances', 'height',	'weight', 'goals', 'assists', 'tackles', 'shots', 'keyPasses', 'cleanSheets']
col_gk = ['name', 'appearances', 'height',	'weight', 'saves', 'cleanSheets', 'goalsConceded']


for season in list(df_player_lag['season'].unique()):
    for team in df_player_lag['team'].unique():
        if df_player_lag[(df_player_lag['season']==season) & (df_player_lag['team']==team)].shape[0] > 11:

            team_dict['season'].append(season)
            team_dict['team'].append(team)

            #players
            df_f = df_player_lag[(df_player_lag['season']==int(season)) & (df_player_lag['team']==str(team)) & (df_player_lag['position']=='F')].sort_values(by='appearances', ascending=False)[:3]
            df_m = df_player_lag[(df_player_lag['season']==int(season)) & (df_player_lag['team']==team) & (df_player_lag['position']=='M')].sort_values(by='appearances', ascending=False)[:6]
            df_d = df_player_lag[(df_player_lag['season']==int(season)) & (df_player_lag['team']==team) & (df_player_lag['position']=='D')].sort_values(by='appearances', ascending=False)[:7]

            team_dict = flatten_team(df_f, team_dict, col_players, 'F')
            team_dict = flatten_team(df_m, team_dict, col_players, 'M')
            team_dict = flatten_team(df_d, team_dict, col_players, 'D')

            #goalkeepers
            df_gk = df_goal_lag[(df_goal_lag['season']==int(season)) & (df_goal_lag['team']==team)].sort_values(by='appearances', ascending=False)[:1]
            team_dict = flatten_team(df_gk, team_dict, col_gk, 'GK')

df_team_players = pd.DataFrame(team_dict)

Датасет, где результаты последних 10 матчей команды (лаги)

In [399]:
df_res_home = df[['match_id', 'teams_team_1_name', 'team_1_hue']]
df_res_guest = df[['match_id', 'teams_team_2_name', 'team_1_hue']]
df_res_guest['team_1_hue'].replace({1:0, 0:1}, inplace=True)

df_res_home.rename(columns={'teams_team_1_name':'team', 'team_1_hue': 'result'}, inplace=True)
df_res_guest.rename(columns={'teams_team_2_name':'team', 'team_1_hue': 'result'}, inplace=True)

In [400]:
print(df_res_home.shape, df_res_guest.shape)

(3800, 3) (3800, 3)


In [401]:
df_res = pd.concat([df_res_home, df_res_guest], axis=0)
df_res.sort_values(by='match_id', inplace=True)
df_res.reset_index(drop=True, inplace=True)
df_res.shape

(7600, 3)

In [402]:
df_res.head()

match_id               team  result
0      9611     Crystal Palace       0
1      9611            Arsenal       1
2      9612            Everton       2
3      9612     Leicester City       2
4      9613  Manchester United       0

In [403]:
team_lag = 6
df_team_lag = pd.DataFrame(columns=df_res.columns.tolist() + ['result_lag_' + str(i) for i in range(1, team_lag)])
for team in df_res['team'].unique():
    df_temp = df_res[df_res['team']==team]
    for i in range(1, team_lag):
        lag = df_temp['result'].shift(i)
        df_temp['result_lag_' + str(i)] = lag

    df_team_lag = pd.concat([df_team_lag, df_temp], axis=0)


In [404]:
df_team_lag.drop('result', axis=1, inplace=True)

Датасет с лагами по результатам матчей между командами

In [405]:
t = df[['match_id', 'teams_team_1_name', 'teams_team_2_name', 'team_1_hue']]

In [406]:
#Датефрейм который агригирует результаты команды независимо от того, играла она дома или в гостях
df_game_team = pd.DataFrame(columns=t.columns)

for team_1 in t['teams_team_1_name'].unique():
    for team_2 in t['teams_team_2_name'].unique():
        df_temp_1 = t[(t['teams_team_1_name']==team_1) & (t['teams_team_2_name']==team_2)]
        df_temp_2 = t[(t['teams_team_1_name']==team_2) & (t['teams_team_2_name']==team_1)]

        df_temp_2['team_1_hue'].replace({1:0, 0:1}, inplace=True)
        df_temp_2.rename(columns={'teams_team_1_name':'teams_team_2_name', 'teams_team_2_name':'teams_team_1_name'}, inplace=True)

        df_temp = pd.concat([df_temp_1, df_temp_2], axis=0)

        df_game_team = pd.concat([df_game_team, df_temp], axis=0)

df_game_team.sort_values(by='match_id', inplace=True)                   

In [407]:
df_game_team

match_id  teams_team_1_name  teams_team_2_name team_1_hue
3793     9611            Arsenal     Crystal Palace          1
3793     9611     Crystal Palace            Arsenal          0
3794     9612     Leicester City            Everton          2
3794     9612            Everton     Leicester City          2
3799     9613  Manchester United       Swansea City          0
...       ...                ...                ...        ...
7       93698         Luton Town             Fulham          0
8       93699    West Ham United    Manchester City          0
8       93699    Manchester City    West Ham United          1
9       93700  Tottenham Hotspur   Sheffield United          1
9       93700   Sheffield United  Tottenham Hotspur          0

[7600 rows x 4 columns]

In [408]:
n_lag = 3
df_game_lag = pd.DataFrame(columns=df_game_team.columns.tolist() + ['game_lag_' + str(i) for i in range(1, n_lag+1)])
for team_1 in df_game_team['teams_team_1_name'].unique():
    for team_2 in df_game_team['teams_team_2_name'].unique():
        df_temp = df_game_team[(df_game_team['teams_team_1_name']==team_1) & (df_game_team['teams_team_2_name']==team_2)]
        #Добавляем лаги
        if df_temp.shape[0] > 0:
            for i in range(1, n_lag+1):
                lag = df_temp['team_1_hue'].shift(i)

                df_temp['game_lag_' + str(i)] = lag
    
        df_game_lag = pd.concat([df_game_lag, df_temp], axis=0)

df_game_lag.sort_values(by='match_id', inplace=True)
df_game_lag.drop('team_1_hue', axis=1, inplace=True)

In [409]:
df_game_lag

match_id  teams_team_1_name  teams_team_2_name game_lag_1 game_lag_2  \
3793     9611            Arsenal     Crystal Palace       None       None   
3793     9611     Crystal Palace            Arsenal       None       None   
3794     9612            Everton     Leicester City       None       None   
3794     9612     Leicester City            Everton       None       None   
3799     9613  Manchester United       Swansea City       None       None   
...       ...                ...                ...        ...        ...   
7       93698             Fulham         Luton Town          1       None   
8       93699    West Ham United    Manchester City          0          0   
8       93699    Manchester City    West Ham United          1          1   
9       93700  Tottenham Hotspur   Sheffield United          1          1   
9       93700   Sheffield United  Tottenham Hotspur          0          0   

     game_lag_3  
3793       None  
3793       None  
3794       None  
3794       None  
3799       None  
...         ...  
7          None  
8             0  
8             1  
9             1  
9             0  

[7600 rows x 6 columns]

In [410]:
#Проверка
t[(t['teams_team_1_name']=='Luton Town') & (t['teams_team_2_name']=='Newcastle United') | (t['teams_team_1_name']=='Newcastle United') & (t['teams_team_2_name']=='Luton Town')]

match_id teams_team_1_name teams_team_2_name  team_1_hue
160     93549  Newcastle United        Luton Town           2
205     93495        Luton Town  Newcastle United           1

Соединим датасеты
df_general  
df_team_players  
df_team_lag по каждой команде  
df_game_lag объединяем по двум командам  

In [411]:
df_general = pd.merge(df_general, df_team_players, left_on=['teams_team_1_name', 'gameweek_compSeason_label'], right_on=['team', 'season'], how='left')
df_general = pd.merge(df_general, df_team_players, left_on=['teams_team_2_name', 'gameweek_compSeason_label'], right_on=['team', 'season'], how='left', suffixes=('_team_1', '_team_2'))

df_general.drop(['season_team_1', 'season_team_2', 'team_team_1', 'team_team_2'], axis=1, inplace=True)

In [412]:
df_general = pd.merge(df_general, df_team_lag, how='left', left_on=['match_id', 'teams_team_1_name'], right_on=['match_id', 'team'])
df_general = pd.merge(df_general, df_team_lag, how='left', left_on=['match_id', 'teams_team_2_name'], right_on=['match_id', 'team'], suffixes=('_team_1', '_team_2'))

df_general.drop(['team_team_1', 'team_team_2'], axis=1, inplace=True)

In [413]:
df_general = pd.merge(df_general, df_game_lag, how='left', on=['match_id', 'teams_team_1_name', 'teams_team_2_name'])

In [414]:
df_general

match_id  gameweek_gameweek  gameweek_compSeason_label  \
0       93700                 38                       2023   
1       93699                 38                       2023   
2       93698                 38                       2023   
3       93697                 38                       2023   
4       93696                 38                       2023   
...       ...                ...                        ...   
3795     9615                  1                       2014   
3796     9614                  1                       2014   
3797     9613                  1                       2014   
3798     9612                  1                       2014   
3799     9611                  1                       2014   

        teams_team_1_name        teams_team_2_name  team_1_hue  \
0        Sheffield United        Tottenham Hotspur           0   
1         Manchester City          West Ham United           1   
2              Luton Town                   Fulham           0   
3               Liverpool  Wolverhampton Wanderers           1   
4          Crystal Palace              Aston Villa           1   
...                   ...                      ...         ...   
3795           Stoke City              Aston Villa           0   
3796  Queens Park Rangers                Hull City           0   
3797    Manchester United             Swansea City           0   
3798       Leicester City                  Everton           2   
3799              Arsenal           Crystal Palace           1   

                   kickoff_label month day_week hour  ground_id  \
0     Sun 19 May 2024, 16:00 BST   May      Sun   16       2003   
1     Sun 19 May 2024, 16:00 BST   May      Sun   16        457   
2     Sun 19 May 2024, 16:00 BST   May      Sun   16       2025   
3     Sun 19 May 2024, 16:00 BST   May      Sun   16       7305   
4     Sun 19 May 2024, 16:00 BST   May      Sun   16         45   
...                          ...   ...      ...  ...        ...   
3795  Sat 16 Aug 2014, 15:00 BST   Aug      Sat   15        435   
3796  Sat 16 Aug 2014, 15:00 BST   Aug      Sat   15         46   
3797  Sat 16 Aug 2014, 12:45 BST   Aug      Sat   12         42   
3798  Sat 16 Aug 2014, 15:00 BST   Aug      Sat   15         49   
3799  Sat 16 Aug 2014, 17:30 BST   Aug      Sat   17         52   

      _accurate_back_zone_pass_team_1  _accurate_chipped_pass_team_1  \
0                         4923.500000                     555.500000   
1                         9053.555556                     732.666667   
2                                 NaN                            NaN   
3                         8856.333333                     844.333333   
4                         5503.111111                     538.000000   
...                               ...                            ...   
3795                      5308.250000                     590.500000   
3796                      4135.000000                     574.000000   
3797                      7671.666667                     724.222222   
3798                      6395.666667                     663.222222   
3799                      7925.444444                     693.777778   

      _accurate_corners_intobox_team_1  _accurate_cross_team_1  \
0                            48.500000              161.500000   
1                            72.555556              173.000000   
2                                  NaN                     NaN   
3                            62.111111              180.222222   
4                            55.666667              165.888889   
...                                ...                     ...   
3795                         53.000000              157.750000   
3796                         67.000000              182.000000   
3797                         49.000000              153.444444   
3798                         46.666667              146.777778   
3799                         51.222222              150.333

In [415]:
df_general[df_general['gameweek_compSeason_label']==2023]

match_id  gameweek_gameweek  gameweek_compSeason_label  \
0      93700                 38                       2023   
1      93699                 38                       2023   
2      93698                 38                       2023   
3      93697                 38                       2023   
4      93696                 38                       2023   
..       ...                ...                        ...   
375    93325                  1                       2023   
376    93324                  1                       2023   
377    93323                  1                       2023   
378    93322                  1                       2023   
379    93321                  1                       2023   

          teams_team_1_name        teams_team_2_name  team_1_hue  \
0          Sheffield United        Tottenham Hotspur           0   
1           Manchester City          West Ham United           1   
2                Luton Town                   Fulham           0   
3                 Liverpool  Wolverhampton Wanderers           1   
4            Crystal Palace              Aston Villa           1   
..                      ...                      ...         ...   
375                 Everton                   Fulham           0   
376  Brighton & Hove Albion               Luton Town           1   
377             Bournemouth          West Ham United           2   
378                 Arsenal        Nottingham Forest           1   
379                 Burnley          Manchester City           0   

                  kickoff_label month day_week hour  ground_id  \
0    Sun 19 May 2024, 16:00 BST   May      Sun   16       2003   
1    Sun 19 May 2024, 16:00 BST   May      Sun   16        457   
2    Sun 19 May 2024, 16:00 BST   May      Sun   16       2025   
3    Sun 19 May 2024, 16:00 BST   May      Sun   16       7305   
4    Sun 19 May 2024, 16:00 BST   May      Sun   16         45   
..                          ...   ...      ...  ...        ...   
375  Sat 12 Aug 2023, 15:00 BST   Aug      Sat   15         31   
376  Sat 12 Aug 2023, 15:00 BST   Aug      Sat   15       7306   
377  Sat 12 Aug 2023, 15:00 BST   Aug      Sat   15        914   
378  Sat 12 Aug 2023, 13:00 BST   Aug      Sat   13         52   
379  Fri 11 Aug 2023, 20:00 BST   Aug      Fri   20         47   

     _accurate_back_zone_pass_team_1  _accurate_chipped_pass_team_1  \
0                        4923.500000                     555.500000   
1                        9053.555556                     732.666667   
2                                NaN                            NaN   
3                        8856.333333                     844.333333   
4                        5503.111111                     538.000000   
..                               ...                            ...   
375                      6304.777778                     615.222222   
376                              NaN                            NaN   
377                      6257.000000                     557.333333   
378                      7925.444444                     693.777778   
379                      4202.000000                     598.428571   

     _accurate_corners_intobox_team_1  _accurate_cross_team_1  \
0                           48.500000              161.500000   
1                           72.555556              173.000000   
2                                 NaN                     NaN   
3                           62.111111              180.222222   
4                           55.666667              165.888889   
..                                ...                     ...   
375                         52.111111              164.666667   
376                               NaN                     NaN   
377                         41.333333              145.333333   
378                         51.222222              150.333333   
379                         52.285714              171.428571   

     _accurate_

In [416]:
df_general['kickoff_label'] = df_general['kickoff_label'].apply(lambda x: parser.parse(x).date())


In [417]:
odds = pd.read_csv('../../../EDA/official/eda_data/df_odds.csv')
features = ['home_name', 'away_name',  'home_avg_odds', 'draw_avg_odds', 'away_avg_odds', 'date']
odds = odds[features]
odds['date'] = odds['date'].apply(lambda x: parser.parse(x).date())

In [418]:
df_general = pd.merge(df_general, odds, how='left', left_on=['teams_team_1_name', 'teams_team_2_name', 'kickoff_label'], right_on=['home_name', 'away_name', 'date'])
drp_list = ['home_name', 'away_name', 'date', 'kickoff_label']
df_general.drop(drp_list, axis=1, inplace=True)
df_general.head()


match_id  gameweek_gameweek  gameweek_compSeason_label teams_team_1_name  \
0    93700                 38                       2023  Sheffield United   
1    93700                 38                       2023  Sheffield United   
2    93699                 38                       2023   Manchester City   
3    93699                 38                       2023   Manchester City   
4    93698                 38                       2023        Luton Town   

   teams_team_2_name  team_1_hue month day_week hour  ground_id  \
0  Tottenham Hotspur           0   May      Sun   16       2003   
1  Tottenham Hotspur           0   May      Sun   16       2003   
2    West Ham United           1   May      Sun   16        457   
3    West Ham United           1   May      Sun   16        457   
4             Fulham           0   May      Sun   16       2025   

   _accurate_back_zone_pass_team_1  _accurate_chipped_pass_team_1  \
0                      4923.500000                     555.500000   
1                      4923.500000                     555.500000   
2                      9053.555556                     732.666667   
3                      9053.555556                     732.666667   
4                              NaN                            NaN   

   _accurate_corners_intobox_team_1  _accurate_cross_team_1  \
0                         48.500000                   161.5   
1                         48.500000                   161.5   
2                         72.555556                   173.0   
3                         72.555556                   173.0   
4                               NaN                     NaN   

   _accurate_cross_nocorner_team_1  _accurate_flick_on_team_1  \
0                       114.500000                  74.500000   
1                       114.500000                  74.500000   
2                       105.777778                  47.888889   
3                       105.777778                  47.888889   
4                              NaN                        NaN   

   _accurate_freekick_cross_team_1  _accurate_fwd_zone_pass_team_1  \
0                             11.0                     6416.000000   
1                             11.0                     6416.000000   
2                             12.0                    12916.444444   
3                             12.0                    12916.444444   
4                              NaN                             NaN   

   _accurate_goal_kicks_team_1  _accurate_keeper_sweeper_team_1  \
0                   100.000000                         9.000000   
1                   100.000000                         9.000000   
2                   128.666667                        23.222222   
3                   128.666667                        23.222222   
4                          NaN                              NaN   

   _accurate_keeper_throws_team_1  _accurate_launches_team_1  \
0                      118.000000                 220.000000   
1                      118.000000                 220.000000   
2                      168.222222                  84.777778   
3                      168.222222                  84.777778   
4                             NaN                        NaN   

   _accurate_layoffs_team_1  _accurate_long_balls_team_1  \
0                132.000000                  1006.500000   
1                132.000000                  1006.500000   
2                383.222222                  1071.666667   
3                383.222222                  1071.666667   
4                       NaN                          NaN   

   _accurate_pass_team_1  _accurate_pull_back_team_1  \
0           11178.000000                   10.500000   
1           11178.000000                   10.500000   
2           21797.111111                   16.444444   
3           21797.111111                   16.444444   
4                    NaN                         NaN   

   _accurate_through_ball_team_1  _acc

In [419]:
df_general.shape

(4300, 1200)

In [420]:
df_general

match_id  gameweek_gameweek  gameweek_compSeason_label  \
0       93700                 38                       2023   
1       93700                 38                       2023   
2       93699                 38                       2023   
3       93699                 38                       2023   
4       93698                 38                       2023   
...       ...                ...                        ...   
4295     9615                  1                       2014   
4296     9614                  1                       2014   
4297     9613                  1                       2014   
4298     9612                  1                       2014   
4299     9611                  1                       2014   

        teams_team_1_name  teams_team_2_name  team_1_hue month day_week hour  \
0        Sheffield United  Tottenham Hotspur           0   May      Sun   16   
1        Sheffield United  Tottenham Hotspur           0   May      Sun   16   
2         Manchester City    West Ham United           1   May      Sun   16   
3         Manchester City    West Ham United           1   May      Sun   16   
4              Luton Town             Fulham           0   May      Sun   16   
...                   ...                ...         ...   ...      ...  ...   
4295           Stoke City        Aston Villa           0   Aug      Sat   15   
4296  Queens Park Rangers          Hull City           0   Aug      Sat   15   
4297    Manchester United       Swansea City           0   Aug      Sat   12   
4298       Leicester City            Everton           2   Aug      Sat   15   
4299              Arsenal     Crystal Palace           1   Aug      Sat   17   

      ground_id  _accurate_back_zone_pass_team_1  \
0          2003                      4923.500000   
1          2003                      4923.500000   
2           457                      9053.555556   
3           457                      9053.555556   
4          2025                              NaN   
...         ...                              ...   
4295        435                      5308.250000   
4296         46                      4135.000000   
4297         42                      7671.666667   
4298         49                      6395.666667   
4299         52                      7925.444444   

      _accurate_chipped_pass_team_1  _accurate_corners_intobox_team_1  \
0                        555.500000                         48.500000   
1                        555.500000                         48.500000   
2                        732.666667                         72.555556   
3                        732.666667                         72.555556   
4                               NaN                               NaN   
...                             ...                               ...   
4295                     590.500000                         53.000000   
4296                     574.000000                         67.000000   
4297                     724.222222                         49.000000   
4298                     663.222222                         46.666667   
4299                     693.777778                         51.222222   

      _accurate_cross_team_1  _accurate_cross_nocorner_team_1  \
0                 161.500000                       114.500000   
1                 161.500000                       114.500000   
2                 173.000000                       105.777778   
3                 173.000000                       105.777778   
4                        NaN                              NaN   
...                      ...                              ...   
4295              157.750000                       106.250000   
4296              182.000000                       116.000000   
4297              153.444444                       107.000000   
4298              146.777778                       102.777778   
4299              150.333333                       101.111111   

    

In [421]:
df_general['match_id'].nunique()
df_general.drop_duplicates(inplace=True)
df_general

match_id  gameweek_gameweek  gameweek_compSeason_label  \
0       93700                 38                       2023   
2       93699                 38                       2023   
4       93698                 38                       2023   
6       93697                 38                       2023   
8       93696                 38                       2023   
...       ...                ...                        ...   
4295     9615                  1                       2014   
4296     9614                  1                       2014   
4297     9613                  1                       2014   
4298     9612                  1                       2014   
4299     9611                  1                       2014   

        teams_team_1_name        teams_team_2_name  team_1_hue month day_week  \
0        Sheffield United        Tottenham Hotspur           0   May      Sun   
2         Manchester City          West Ham United           1   May      Sun   
4              Luton Town                   Fulham           0   May      Sun   
6               Liverpool  Wolverhampton Wanderers           1   May      Sun   
8          Crystal Palace              Aston Villa           1   May      Sun   
...                   ...                      ...         ...   ...      ...   
4295           Stoke City              Aston Villa           0   Aug      Sat   
4296  Queens Park Rangers                Hull City           0   Aug      Sat   
4297    Manchester United             Swansea City           0   Aug      Sat   
4298       Leicester City                  Everton           2   Aug      Sat   
4299              Arsenal           Crystal Palace           1   Aug      Sat   

     hour  ground_id  _accurate_back_zone_pass_team_1  \
0      16       2003                      4923.500000   
2      16        457                      9053.555556   
4      16       2025                              NaN   
6      16       7305                      8856.333333   
8      16         45                      5503.111111   
...   ...        ...                              ...   
4295   15        435                      5308.250000   
4296   15         46                      4135.000000   
4297   12         42                      7671.666667   
4298   15         49                      6395.666667   
4299   17         52                      7925.444444   

      _accurate_chipped_pass_team_1  _accurate_corners_intobox_team_1  \
0                        555.500000                         48.500000   
2                        732.666667                         72.555556   
4                               NaN                               NaN   
6                        844.333333                         62.111111   
8                        538.000000                         55.666667   
...                             ...                               ...   
4295                     590.500000                         53.000000   
4296                     574.000000                         67.000000   
4297                     724.222222                         49.000000   
4298                     663.222222                         46.666667   
4299                     693.777778                         51.222222   

      _accurate_cross_team_1  _accurate_cross_nocorner_team_1  \
0                 161.500000                       114.500000   
2                 173.000000                       105.777778   
4                        NaN                              NaN   
6                 180.222222                       119.888889   
8                 165.888889                       111.333333   
...                      ...                              ...   
4295              157.750000                       106.250000   
4296              182.000000                       116.000000   
4297              153.444444                       107.000000   
4298              146.777778                       102.777778  

In [422]:
df_general[df_general['gameweek_compSeason_label']==2023]

match_id  gameweek_gameweek  gameweek_compSeason_label  \
0      93700                 38                       2023   
2      93699                 38                       2023   
4      93698                 38                       2023   
6      93697                 38                       2023   
8      93696                 38                       2023   
..       ...                ...                        ...   
425    93325                  1                       2023   
426    93324                  1                       2023   
427    93323                  1                       2023   
428    93322                  1                       2023   
429    93321                  1                       2023   

          teams_team_1_name        teams_team_2_name  team_1_hue month  \
0          Sheffield United        Tottenham Hotspur           0   May   
2           Manchester City          West Ham United           1   May   
4                Luton Town                   Fulham           0   May   
6                 Liverpool  Wolverhampton Wanderers           1   May   
8            Crystal Palace              Aston Villa           1   May   
..                      ...                      ...         ...   ...   
425                 Everton                   Fulham           0   Aug   
426  Brighton & Hove Albion               Luton Town           1   Aug   
427             Bournemouth          West Ham United           2   Aug   
428                 Arsenal        Nottingham Forest           1   Aug   
429                 Burnley          Manchester City           0   Aug   

    day_week hour  ground_id  _accurate_back_zone_pass_team_1  \
0        Sun   16       2003                      4923.500000   
2        Sun   16        457                      9053.555556   
4        Sun   16       2025                              NaN   
6        Sun   16       7305                      8856.333333   
8        Sun   16         45                      5503.111111   
..       ...  ...        ...                              ...   
425      Sat   15         31                      6304.777778   
426      Sat   15       7306                              NaN   
427      Sat   15        914                      6257.000000   
428      Sat   13         52                      7925.444444   
429      Fri   20         47                      4202.000000   

     _accurate_chipped_pass_team_1  _accurate_corners_intobox_team_1  \
0                       555.500000                         48.500000   
2                       732.666667                         72.555556   
4                              NaN                               NaN   
6                       844.333333                         62.111111   
8                       538.000000                         55.666667   
..                             ...                               ...   
425                     615.222222                         52.111111   
426                            NaN                               NaN   
427                     557.333333                         41.333333   
428                     693.777778                         51.222222   
429                     598.428571                         52.285714   

     _accurate_cross_team_1  _accurate_cross_nocorner_team_1  \
0                161.500000                       114.500000   
2                173.000000                       105.777778   
4                       NaN                              NaN   
6                180.222222                       119.888889   
8                165.888889                       111.333333   
..                      ...                              ...   
425              164.666667                       113.333333   
426                     NaN                              NaN   
427              145.333333                       105.833333   
428              150.333333                       101.111111   
429              171

In [423]:
df_simple

match_id  gameweek_compSeason_label  gameweek_gameweek  \
379     93321                       2023                  1   
378     93322                       2023                  1   
374     93323                       2023                  1   
375     93324                       2023                  1   
376     93325                       2023                  1   
..        ...                        ...                ...   
5       93696                       2023                 38   
6       93697                       2023                 38   
7       93698                       2023                 38   
8       93699                       2023                 38   
9       93700                       2023                 38   

           kickoff_label       teams_team_1_name        teams_team_2_name  \
379  2023-08-11 20:00:00                 Burnley          Manchester City   
378  2023-08-12 13:00:00                 Arsenal        Nottingham Forest   
374  2023-08-12 15:00:00             Bournemouth          West Ham United   
375  2023-08-12 15:00:00  Brighton & Hove Albion               Luton Town   
376  2023-08-12 15:00:00                 Everton                   Fulham   
..                   ...                     ...                      ...   
5    2024-05-19 16:00:00          Crystal Palace              Aston Villa   
6    2024-05-19 16:00:00               Liverpool  Wolverhampton Wanderers   
7    2024-05-19 16:00:00              Luton Town                   Fulham   
8    2024-05-19 16:00:00         Manchester City          West Ham United   
9    2024-05-19 16:00:00        Sheffield United        Tottenham Hotspur   

                  ground_name  
379                 Turf Moor  
378          Emirates Stadium  
374          Vitality Stadium  
375  American Express Stadium  
376             Goodison Park  
..                        ...  
5               Selhurst Park  
6                     Anfield  
7             Kenilworth Road  
8              Etihad Stadium  
9                Bramall Lane  

[380 rows x 7 columns]

In [424]:
df_general.sort_values(by=['match_id'], inplace=True)

In [425]:
df_general.to_csv(Path('data/df_general.csv').resolve(), index=False)